In [207]:
import numpy as np
import pandas as pd
from matplotlib import pyplot as plt
import re
from typing import List

In [185]:
# load trainer data
trainer = pd.read_csv(r'../data/raw/ds_pokemon_trainer_application_data.csv')
trainer.head()

C:\Users\elove\AppData\Local\Temp\ipykernel_18768\2541563265.py:2: DtypeWarning: Columns (69,70,71,72) have mixed types. Specify dtype option on import or set low_memory=False.
  trainer = pd.read_csv(r'../data/raw/ds_pokemon_trainer_application_data.csv')


ApplicationStatus ApplicationType   ApplyDate CurrentlyEmployed  \
0   Filed Not Hired       Applicant  2013-11-26             False   
1   Filed Not Hired       Applicant  2013-11-27              True   
2   Filed Not Hired       Applicant  2013-11-22               NaN   
3   Filed Not Hired       Applicant  2013-11-23              True   
4               New       Applicant  2013-11-23              True   

  CurrentlyTrainingPokemon CurrentlyWorkInThisRegion  GraduateSchoolGPA  \
0                      NaN                     False                NaN   
1                      NaN                     False                NaN   
2                      NaN                     False                NaN   
3                      NaN                     False                NaN   
4                      NaN                     False                NaN   

  GraduateSchoolGraduate GymBadge1Pokemon GymBadge2Pokemon GymBadge3Pokemon  \
0                    NaN              NaN              NaN              NaN   
1                    NaN              NaN              NaN              NaN   
2                    NaN              NaN              NaN              NaN   
3                    NaN           Seedot              NaN              NaN   
4                    NaN              NaN              NaN              NaN   

  GymBadge4Pokemon GymBadgePerm1 GymBadgePerm2 GymBadgePerm3 GymBadgePerm4  \
0              NaN         False         False         False         False   
1              NaN         False         False         False         False   
2              NaN         False         False         False         False   
3              NaN         False         False         False         False   
4              NaN         False         False         False         False   

  GymBadgeTemp1 GymBadgeTemp2 GymBadgeTemp3 GymBadgeTemp4  \
0         False         False         False         False   
1         False         False         False         False   
2         False         False         False         False   
3         False         False         False         False   
4         False         False         False         False   

  GymCertificationEverSuspended GymCertified HighEduLevelCompleted  \
0                           NaN          NaN                    HS   
1                         False        False                HS/GED   
2                           NaN          NaN             Bachelors   
3                         False        False                    AD   
4                           NaN          NaN            Associates   

   HighSchoolGPA HighSchoolGraduate HiredSalaryOffer  InternalEmployee  \
0           3.50                Yes              NaN             False   
1           3.68                Yes              NaN             False   
2           3.80                Yes              NaN             False   
3           2.30                Yes              NaN             False   
4           3.00                Yes              NaN             False   

  JobPostingDate JobSchedule JobShiftDay JobShiftEvening JobShiftNight  \
0     2013-11-19         PRN        True           False         False   
1     2013-11-19         PRN        True            True          True   
2     2013-10-29   Full-time        True            True          True   
3     2013-11-19         PRN        True            True          True   
4     2013-10-29   Full-time        True            True          True   

  JobShiftRotating JobShiftWeekend JobStatusFlexTime JobStatusFullTime  \
0            False           False             False              True   
1             True            True              True              True   
2             True            True             False              True   
3             True            True              True              True   
4             True            True             False              True   

  JobStatusPartTime JobStatusPerDiem JobStatusTemp LastPerformaceRati

In [186]:
trainer.describe()

GraduateSchoolGPA  HighSchoolGPA  OtherSchoolGPA  TechnicalSchoolGPA  \
count        3889.000000   27206.000000     3781.000000        10241.000000   
mean            3.478934       3.203623        3.463853            3.477138   
std             0.476177       0.516601        0.482387            0.478480   
min             0.000000       0.000000        0.000000            0.000000   
25%             3.200000       3.000000        3.070000            3.000000   
50%             3.550000       3.200000        3.500000            3.500000   
75%             3.800000       3.570000        3.890000            3.900000   
max             4.300000       4.300000        4.200000            4.300000   

       TotalYearsOfExp  UndergradSchoolGPA         hired  
count     96914.000000        24361.000000  96321.000000  
mean          4.154095            3.213768      0.017213  
std           3.469671            0.451540      0.130066  
min           1.000000            0.000000      0.000000  
25%           1.000000            3.000000      0.000000  
50%           3.000000            3.200000      0.000000  
75%           9.000000            3.500000      0.000000  
max          10.000000            4.300000      1.000000

In [187]:
# load pokemon names
pokemon = pd.read_csv(r'../data/raw/ds_pokemon_names.csv', header=None)
pokemon.head()

# this is simply a list of pokemon names and not very useful here.
# if it had a foreign key to match with a trainer, we could use it. for now, skipping further analysis.

0
0    Glaceon
1     Seedot
2     Mareep
3     Audino
4  Bellossom

In [190]:
# missing data identification
# many missing values; small number of missing values in target variable (hired)
pd.set_option('display.max_rows', None)

trainer_na = pd.DataFrame(trainer.isnull().sum()/len(trainer),
                          columns=['percent_na'])
trainer_na.sort_values(by='percent_na', ascending=False)

percent_na
HiredSalaryOffer                                  0.98721
GymBadge4Pokemon                                  0.98188
OtherSchoolGPA                                    0.96219
GraduateSchoolGPA                                 0.96111
CurrentlyTrainingPokemon                          0.96089
GymBadge3Pokemon                                  0.94099
WorkingForJobAppliedFor                           0.93855
LastPerformaceRating                              0.93855
SpokenWithCurrentBoss                             0.93855
GraduateSchoolGraduate                            0.90211
TechnicalSchoolGPA                                0.89759
OtherSchoolGraduate                               0.85856
GymBadge2Pokemon                                  0.83589
RecentTrainingExperience4Pokemon                  0.83035
UndergradSchoolGPA                                0.75639
RecentTrainingExperience4PayRateEnd               0.74032
HighSchoolGPA                                     0.72794
RecentTrainingExperience4To                       0.69623
RecentTrainingExperience4From                     0.69261
RecentTrainingExperience3Pokemon                  0.68751
RecentTrainingExperience4ContactForRef            0.68131
RecentTrainingExperience4EmploymentStatus         0.67083
TechnicalSchoolGraduate                           0.66524
GymBadge1Pokemon                                  0.65027
RecentTrainingExperienceContactForRefYes          0.60166
RecentTrainingExperienceContactForRefNA           0.60166
RecentTrainingExperienceContactForRefNo           0.60166
RecentTrainingExperienceContactForRefPostHire     0.60166
RecentTrainingExperience2Pokemon                  0.58093
RecentTrainingExperience3PayRateEnd               0.55162
GymCertified                                      0.52953
UndergradSchoolGraduate                           0.49280
GymCertificationEverSuspended                     0.47353
RecentTrainingExperience1Pokemon                  0.47054
RecentTrainingExperience3ContactForRef            0.46605
RecentTrainingExperience3EmploymentStatus         0.45681
RecentTrainingExperience3To                       0.44762
RecentTrainingExperience3From                     0.44133
ReferenceRelationship3                            0.39644
RecentTrainingExperience2PayRateEnd               0.39283
ReferenceRelationship2                            0.35964
ReferenceRelationship1                            0.33530
RecentTrainingExperience1PayRateEnd               0.29319
RecentTrainingExperience2ContactForRef            0.27535
RecentTrainingExperience2EmploymentStatus         0.26935
RecentTrainingExperience2To                       0.26552
RecentTrainingExperience2From                     0.25321
PositionForTrainingPokemon                        0.24804
CurrentlyEmployed                                 0.17404
RecentTrainingExperience1To                       0.13660
RecentTrainingExperience1EmploymentStatus         0.10624
WorkedInThisRegion                                0.09378
HighSchoolGraduate                                0.07867
CurrentlyWorkInThisRegion                         0.07518
RecentTrainingExperience1ContactForRef            0.06530
GymBadgeTemp2                                     0.06527
GymBadgeTemp3                                     0.06527
GymBadgePerm4                                     0.06527
GymBadgeTemp4                                     0.06527
GymBadgePerm3                                     0.06527
GymBadgePerm2                                     0.06527
GymBadgePerm1                                     0.06527
GymBadgeTemp1                                     0.06527
RecentTrainingExperience1From                     0.05160
hired                                             0.03679
TotalYearsOfExp                                   0.03086
JobPostingDate                                    0.01500
HighEduLevelCompleted                             0.01188
JobSchedule                                  

In [191]:
pd.reset_option('display.max_rows')

In [192]:
# feature engineering

# many missing values seem to be from missing application work histories and education histories
# we should combine these into features to view highest level of education, number of jobs etc.

trainer_cleaned = trainer.copy()

# references
trainer['RecentTrainingExperience1ContactForRef'].tolist()
references = ['RecentTrainingExperience1ContactForRef','RecentTrainingExperience2ContactForRef',
              'RecentTrainingExperience3ContactForRef','RecentTrainingExperience4ContactForRef']
trainer['recent_reference_provided'] = np.where(trainer['RecentTrainingExperience1ContactForRef']==True, True, False)
trainer.drop(columns=references, inplace=True)

In [216]:
# pay rate
def extract_pay_type(pay_rate: str):
    pay_type = re.sub('[0-9\.\s]','', pay_rate)
        
    return pay_type

def extract_pay_amt(pay_rate: str):
    pay_amt = re.sub('[\s_a-zA-Z]','', pay_rate)
    
    return pay_amt

def convert_to_numeric(df: pd.DataFrame, cols: List[str]):
    df = pd.to_numeric(df[cols], errors='coerce')

In [217]:
# highest pay rate
trainer['RecentTrainingExperience1PayRateEnd'].unique()
pay_rate = {'RecentTrainingExperience1PayRateEnd': ['pay_type_1', 'pay_amt_1'],
            'RecentTrainingExperience2PayRateEnd': ['pay_type_2', 'pay_amt_2'],
            'RecentTrainingExperience3PayRateEnd': ['pay_type_3', 'pay_amt_3'],
            'RecentTrainingExperience4PayRateEnd': ['pay_type_4', 'pay_amt_4']}

# print(rates)

for key, _ in pay_rate.items():
    trainer[key] = trainer[key].apply(str)

for key, value in pay_rate.items():
    trainer[value[0]] = trainer[key].apply(lambda row: extract_pay_type(pay_rate=row))

for key, value in pay_rate.items():
    trainer[value[1]] = trainer[key].apply(lambda row: extract_pay_amt(pay_rate=row))
    trainer[value[1]] = pd.to_numeric(trainer[value[1]], errors='coerce')
    
# clean missing values


In [223]:
pd.set_option('display.max_rows', None)


trainer['pay_amt_2'].sort_values()

35407    0.000000e+00
9632     0.000000e+00
80326    0.000000e+00
23467    0.000000e+00
14761    0.000000e+00
10001    0.000000e+00
92613    0.000000e+00
58777    0.000000e+00
23218    0.000000e+00
43363    0.000000e+00
80322    0.000000e+00
67330    0.000000e+00
39828    0.000000e+00
21989    0.000000e+00
18903    0.000000e+00
7392     0.000000e+00
33817    0.000000e+00
14736    0.000000e+00
21471    0.000000e+00
54330    0.000000e+00
14698    0.000000e+00
14712    0.000000e+00
14716    0.000000e+00
1443     0.000000e+00
11402    0.000000e+00
3629     0.000000e+00
24593    0.000000e+00
51293    0.000000e+00
72306    0.000000e+00
21938    0.000000e+00
85761    0.000000e+00
13272    0.000000e+00
78419    0.000000e+00
77780    0.000000e+00
11351    0.000000e+00
51326    0.000000e+00
72296    0.000000e+00
14854    0.000000e+00
30231    0.000000e+00
3659     0.000000e+00
33771    0.000000e+00
25207    0.000000e+00
1349     0.000000e+00
18858    0.000000e+00
68901    0.000000e+00
25534    0

In [225]:
trainer['RecentTrainingExperience1PayRateEnd'].sort_values()

22950            0.00 PER_HOUR
40322            0.00 PER_HOUR
1169             0.00 PER_HOUR
83340            0.00 PER_HOUR
83339            0.00 PER_HOUR
17247            0.00 PER_HOUR
1162             0.00 PER_HOUR
35365            0.00 PER_HOUR
1173             0.00 PER_HOUR
53576            0.00 PER_HOUR
81494            0.00 PER_HOUR
42303            0.00 PER_HOUR
89819            0.00 PER_HOUR
40346            0.00 PER_HOUR
70107            0.00 PER_HOUR
22371            0.00 PER_HOUR
31212            0.00 PER_HOUR
1152             0.00 PER_HOUR
26857            0.00 PER_HOUR
47957            0.00 PER_HOUR
1182             0.00 PER_HOUR
69924            0.00 PER_HOUR
41866            0.00 PER_HOUR
10001            0.00 PER_HOUR
55193            0.00 PER_HOUR
35241            0.00 PER_HOUR
26831            0.00 PER_HOUR
26834            0.00 PER_HOUR
10035            0.00 PER_HOUR
26837            0.00 PER_HOUR
85635            0.00 PER_HOUR
78215            0.00 PER_HOUR
22355   

In [ ]:
'hired',
'HiredSalaryOffer',
'GymBadge4Pokemon',
'CurrentlyTrainingPokemon',
'WorkingForJobAppliedFor',
'LastPerformaceRating',
'GymCertified'